In [16]:
# import standard libraries
import numpy as np

import warnings
import pandas as pd

from pandas.core.common import SettingWithCopyWarning
warnings.simplefilter(action="ignore", category=SettingWithCopyWarning)

import datetime
import pickle
from nltk.corpus import stopwords
import re
import regex
import string
from urllib.parse import urlparse

In [17]:
# import ML libraries
import torch
from torch import nn
from torch.utils.data import DataLoader
from torchvision import datasets
from torchvision.transforms import ToTensor
from torch.utils.data import Dataset

In [18]:
# import training data
with open("../data/training_data", "rb") as fb:
    training_data = pickle.load(fb)

In [19]:
# import testing data
with open("../data/testing_data", "rb") as fb:
    testing_data = pickle.load(fb)

In [20]:
# try set gpu as training device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device)

cuda


In [21]:
# preprocessing
training_data = training_data.loc[training_data.type == "story"]
testing_data = testing_data.loc[testing_data.type == "story"]

In [22]:
training_data_indexed = training_data.reset_index(drop=True)
testing_data_indexed = testing_data.reset_index(drop=True)
print(training_data_indexed)

                                                    title  \
0       Not sure if this is legal for US citizens but ...   
1       What happens to Americans who film police viol...   
2                                                     NaN   
3       Big data startup Gainsight uses big data to im...   
4                                                     NaN   
...                                                   ...   
457818  US lawmaker injects ISP throttle into Obama re...   
457819           Failure-Oblivious Computing (2004) [pdf]   
457820  Everything I Needed to Know I Learned in Math ...   
457821   Twitter employee live tweets WSOP from the table   
457822  Deep-learning vision system anticipates human ...   

                                                      url text  dead  \
0                                        https://betco.in  NaN   NaN   
1       http://www.theguardian.com/us-news/2015/aug/15...  NaN   NaN   
2                                                  

In [23]:
# define preproccessing function
stop_words = set(stopwords.words('english'))

def preproccess(text):
    if isinstance(text, float):
        return [""]
    
    # split into tokens
    tokens = re.split('\s+', text)

    # remove punctuation
    tokens = ["".join([i for i in x if i not in string.punctuation]) for x in tokens]

    # remove numbers
    tokens = [re.sub("\d+", "", x) for x in tokens]

    # make all tokens lowercase
    tokens = [x.lower() for x in tokens]

    # remove tokens which are too short or too long
    tokens = [token for token in tokens if len(token) > 2 and len(token) < 15]

    # remove hyperlinks
    tokens = [token for token in tokens if not (token.startswith("http") or token.startswith("www") or token.endswith("com"))]

    # remove stop words
    final = [word for word in tokens if word not in stop_words]

    if isinstance(final, float):
        return [""]

    return final

In [24]:
# apply preproccessing 

#training_titles_processed = [preproccess(x) for x in training_data_indexed["title"]]
#training_text_processed = [preproccess(x) for x in training_data_indexed["text"]]
training_titles_processed = training_data_indexed["title"].apply(lambda x: preproccess(x))
training_text_processed = training_data_indexed["text"].apply(lambda x: preproccess(x))
testing_titles_processed = testing_data_indexed["title"].apply(lambda x: preproccess(x))
testing_text_processed = testing_data_indexed["text"].apply(lambda x: preproccess(x))

In [25]:
# get unique words for titles
titles_vocab_train = list(dict.fromkeys(training_titles_processed.apply(pd.Series).stack().reset_index(drop = True)))
titles_vocab_test = list(dict.fromkeys(testing_titles_processed.apply(pd.Series).stack().reset_index(drop = True)))
titles_vocab = list(dict.fromkeys(titles_vocab_train + titles_vocab_test))


In [26]:
# get unique words for texts
text_vocab_train = list(dict.fromkeys(training_text_processed.apply(pd.Series).stack().reset_index(drop = True)))
text_vocab_test = list(dict.fromkeys(testing_text_processed.apply(pd.Series).stack().reset_index(drop = True)))
text_vocab = list(dict.fromkeys(text_vocab_train + text_vocab_test))


In [27]:
# save created vocabs
with open("titles_vocab", "wb") as fb:
    pickle.dump(titles_vocab, fb)

with open("text_vocab", "wb") as fb:
    pickle.dump(text_vocab, fb)


In [28]:
# load created vocabs
with open("titles_vocab", "rb") as fb:
    titles_vocab = pickle.load(fb)

with open("text_vocab", "rb") as fb:
    text_vocab = pickle.load(fb)

In [29]:
print(titles_vocab)

['sure', 'legal', 'citizens', 'play', 'poker', 'happens', 'americans', 'film', 'police', 'violence', '', 'big', 'data', 'startup', 'gainsight', 'uses', 'improve', 'customer', 'retention', 'listen', 'chi', 'google', 'faces', 'million', 'lawsuit', 'android', 'location', 'tracking', 'dwollas', 'centers', 'pci', 'compliant', 'devart', 'art', 'made', 'code', 'autonomous', 'weapons', 'operational', 'risk', 'ethical', 'autonomy', 'project', 'pdf', 'mozilla', 'firefox', 'startsida', 'article', 'written', 'old', 'fashioned', 'way', 'command', 'line', 'glory', 'pergamon', 'new', 'york', 'nsw', 'seeks', 'build', 'unhackable', 'netbook', 'network', 'hot', 'recurring', 'series', 'revolutions', 'fend', 'microsoft', 'slack’s', 'ceo', 'tackling', 'complaints', 'everything', 'need', 'know', 'rebuild', 'civilization', 'scratch', 'announcing', 'free', 'marketing', 'automation', 'everyone', 'hightrack', 'productivity', 'app', 'tasks', 'calendar', 'andme', 'david', 'brooks', 'intellectual', 'collapse', 'ce

In [30]:
# add a special empty token for posts with empty titles or text
titles_vocab.append("<|empty|>")
text_vocab.append("<|empty|>")

In [31]:
print(training_data_indexed.loc[0])

title          Not sure if this is legal for US citizens but ...
url                                             https://betco.in
text                                                         NaN
dead                                                         NaN
by                                                  dickchaninin
score                                                        3.0
time                                                1304882921.0
type                                                       story
id                                                       2526540
parent                                                       NaN
descendants                                                  0.0
ranking                                                      NaN
deleted                                                      NaN
timestamp                                   2011-05-08T19:28:41Z
dates                                        2011-05-08 20:28:41
Name: 0, dtype: object


In [32]:
# define cols which are used in model
req_cols_with_url = ["title", "url", "text", "time"]
req_cols_without_url = ["title", "text", "time"]

In [33]:
# extract specific cols needed
scores = training_data_indexed.score
training_data_indexed = training_data_indexed[req_cols_without_url]

testing_scores = testing_data_indexed.score
testing_data_indexed = testing_data_indexed[req_cols_without_url]

In [34]:
print(training_data_indexed.loc[0])

title    Not sure if this is legal for US citizens but ...
text                                                   NaN
time                                          1304882921.0
Name: 0, dtype: object


In [35]:
# define basic Bag of Words function
def BOW_bin(words, vocab):
    return [1 if word in words else 0 for word in vocab]

def BOW_freq(words, vocab):
    return [words.count(word) for word in vocab]

In [36]:
# Function for getting domain name form url
def extract_domain(url):
    if not isinstance(url, str):
        return ""
    return urlparse(url).netloc

In [37]:
# define transformations of the data

class TextualTransform1(object):

    def __call__(self, sample):
        post, score = sample["post"], sample["score"]
        
        post["title"] = BOW_bin(preproccess(post["title"]), titles_vocab)
        post["text"] = BOW_bin(preproccess(post["text"]), text_vocab)

        return {'post': post, 'score': score}

class TextualTransform2(object):

    def __call__(self, sample):
        post, score = sample["post"], sample["score"]
        
        post["title"] = BOW_freq(preproccess(post["title"]), titles_vocab)
        post["text"] = BOW_freq(preproccess(post["text"]), text_vocab)

        return {'post': post, 'score': score}

class URLTransform(object):

    def __call__(self, sample):
        post, score = sample["post"], sample["score"]

        post["url"] = extract_domain(post["url"])

        return {'post': post, 'score': score}

class TensorTransform(object):

    def __call__(self, sample):
        post, score = sample["post"], sample["score"]

        title_list = post["title"]
        text_list = post["text"]
        time = post["time"]
        
        output = title_list + text_list
        output.append(time)

        output = torch.FloatTensor(output)
        score = torch.FloatTensor(score)

        return {"post": output, "score": score}
        


        


In [38]:
# define custom dataset for BoW model
class HackerNewsPostDataset(Dataset):

    def __init__(self, data, labels, cutoff = None, transforms = None):
        self.posts = data
        self.scores = labels
        self.transforms = transforms
        self.cutoff = cutoff

    def __len__(self):
        return len(self.posts)

    def __getitem__(self, index):
        if torch.is_tensor(index):
            index = index.tolist()

        post = self.posts.loc[index]
        score = self.scores[index]

        if self.cutoff:
            score = [(1 if isinstance(score, float) and score > self.cutoff else 0)]

        sample = {'post': post, 'score': score}

        if self.transforms:
            for transform in self.transforms:
                sample = transform(sample)

        return sample

In [81]:
# define a index dict for getting word embeddings
titles_to_index = {word: index for index, word in enumerate(titles_vocab)}
text_to_index = {word: index + len(titles_to_index) for index, word in enumerate(text_vocab)}

In [84]:
print(titles_to_index)

{'sure': 0, 'legal': 1, 'citizens': 2, 'play': 3, 'poker': 4, 'happens': 5, 'americans': 6, 'film': 7, 'police': 8, 'violence': 9, '': 10, 'big': 11, 'data': 12, 'startup': 13, 'gainsight': 14, 'uses': 15, 'improve': 16, 'customer': 17, 'retention': 18, 'listen': 19, 'chi': 20, 'google': 21, 'faces': 22, 'million': 23, 'lawsuit': 24, 'android': 25, 'location': 26, 'tracking': 27, 'dwollas': 28, 'centers': 29, 'pci': 30, 'compliant': 31, 'devart': 32, 'art': 33, 'made': 34, 'code': 35, 'autonomous': 36, 'weapons': 37, 'operational': 38, 'risk': 39, 'ethical': 40, 'autonomy': 41, 'project': 42, 'pdf': 43, 'mozilla': 44, 'firefox': 45, 'startsida': 46, 'article': 47, 'written': 48, 'old': 49, 'fashioned': 50, 'way': 51, 'command': 52, 'line': 53, 'glory': 54, 'pergamon': 55, 'new': 56, 'york': 57, 'nsw': 58, 'seeks': 59, 'build': 60, 'unhackable': 61, 'netbook': 62, 'network': 63, 'hot': 64, 'recurring': 65, 'series': 66, 'revolutions': 67, 'fend': 68, 'microsoft': 69, 'slack’s': 70, 'ceo

In [85]:
# define custom dataset for word embeddings model
class EmbeddingsDataset(Dataset):

    def __init__(self, data, lables, cutoff):
        self.posts = data
        self.scores = lables
        self.cutoff = cutoff

    def __len__(self):
        return len(self.posts)

    def __getitem__(self, index):

        post = self.posts.loc[index]
        score = self.scores[index]

        title_indexs = preproccess(post["title"])
        text_indexs = preproccess(post["text"])

        if title_indexs == []:
            title_indexs = ["<|empty|>"]

        if text_indexs == []:
            text_indexs = ["<|empty|>"]

        time = post["time"]

        score = 1 if (isinstance(score, float) and score > self.cutoff) else 0

        #score = torch.FloatTensor(score)

        sample = ((title_indexs, text_indexs, time), score)
        return sample


In [86]:
# non url training dataset for BoW model
transforms = [TextualTransform1(), TensorTransform()]
cutoff = 20

post_training_dataset = HackerNewsPostDataset(training_data_indexed, scores, cutoff, transforms)
post_testing_dataset = HackerNewsPostDataset(testing_data_indexed, testing_scores, cutoff, transforms)

In [87]:
# create embedding datasets
embedding_dataset_train = EmbeddingsDataset(training_data_indexed, scores, cutoff)
embedding_dataset_test = EmbeddingsDataset(testing_data_indexed, testing_scores, cutoff)

In [88]:
# As dataset is imbalanced define a weighted sampler
from torch.utils.data import WeightedRandomSampler

num_popular = (scores > cutoff).sum()

unpopular_weight = 1
popular_weight = (len(embedding_dataset_train) - num_popular) / num_popular


class_weights = [unpopular_weight, popular_weight]
weights = [0] * len(embedding_dataset_train)

for index, score in enumerate(scores):
    weight = class_weights[int(score > cutoff)]
    weights[index] = weight

sampler = WeightedRandomSampler(weights, num_samples = len(weights), replacement = True)

In [89]:
print(unpopular_weight, popular_weight)

1 11.369248642368897


In [90]:
embedding_dataset_train[0]

((['sure', 'legal', 'citizens', 'play', 'poker'], [''], 1304882921.0), 0)

In [91]:
# define function for collating batches
def collate_batch_embed(batch):
    lables, texts, offsets = [], [], [0]
    for post, score in batch:

        titles_indexs = [titles_to_index[word] for word in post[0]]
        text_indexs = [text_to_index[word] for word in post[1]]
        
        proccessed_input = torch.tensor(titles_indexs + text_indexs, dtype = torch.int64).to(device)

        texts.append(proccessed_input)
        lables.append([score])
        offsets.append(proccessed_input.size(0))

    lables = torch.tensor(lables, dtype = torch.int64).to(device)
    offsets = torch.tensor(offsets[:-1]).cumsum(dim = 0).to(device)
    texts = torch.cat(texts)
    return lables, texts, offsets



In [92]:
print(post_testing_dataset[0])

{'post': tensor([0.0000e+00, 0.0000e+00, 0.0000e+00,  ..., 0.0000e+00, 0.0000e+00,
        1.4248e+09]), 'score': tensor([0.])}


In [93]:
1960 * 5

9800

In [94]:
# create dataloaders
batch_size = 128
num_iterations = 9800
num_epochs = 5
train_loader = torch.utils.data.DataLoader(dataset=post_training_dataset, batch_size=batch_size, shuffle=True)

In [95]:
test_loader = torch.utils.data.DataLoader(dataset=post_testing_dataset, batch_size=100, shuffle=True)

In [96]:
train_loader_embed = torch.utils.data.DataLoader(dataset = embedding_dataset_train, batch_size=batch_size, sampler=sampler, 
                                                collate_fn = collate_batch_embed)
test_loader_embed = torch.utils.data.DataLoader(dataset = embedding_dataset_test, batch_size=batch_size, sampler=sampler, 
                                                collate_fn = collate_batch_embed)

In [52]:
it = iter(train_loader_embed)
first = next(it)
print(len(first[0]), first[0])
print(len(first[1]))
print(len(first[2]), first[2])

128 tensor([[1],
        [0],
        [1],
        [1],
        [1],
        [0],
        [1],
        [0],
        [1],
        [1],
        [1],
        [0],
        [0],
        [1],
        [0],
        [1],
        [1],
        [1],
        [1],
        [1],
        [0],
        [0],
        [0],
        [0],
        [0],
        [0],
        [0],
        [0],
        [1],
        [0],
        [1],
        [1],
        [0],
        [0],
        [1],
        [0],
        [1],
        [0],
        [0],
        [1],
        [0],
        [0],
        [0],
        [0],
        [0],
        [0],
        [0],
        [1],
        [0],
        [0],
        [1],
        [0],
        [1],
        [0],
        [1],
        [0],
        [0],
        [0],
        [1],
        [1],
        [1],
        [0],
        [0],
        [1],
        [1],
        [1],
        [1],
        [0],
        [1],
        [0],
        [0],
        [1],
        [0],
        [0],
        [0],
        [1],
        

In [97]:
# basic Feed Forward Neural Network

class FFNetwork(nn.Module):
    def __init__(self, input_dimensions, hidden_dimensions, output_dimensions):
        super(FFNetwork, self).__init__()

        self.linear1 = nn.Linear(input_dimensions, hidden_dimensions)

        self.nonlinear = nn.ReLU()
    
        self.linear2 = nn.Linear(hidden_dimensions, output_dimensions)

        self.sigmoid = torch.sigmoid
    
    def forward(self, x):

        x = self.linear1(x)

        x = self.nonlinear(x)

        output = self.linear2(x)

        output = self.sigmoid(output)
        return output
        

In [98]:
# basic Feed Forward Neural Network (Regression)

class FFNetworkReg(nn.Module):
    def __init__(self, input_dimensions, hidden_dimensions, output_dimensions):
        super(FFNetworkReg, self).__init__()

        self.linear1 = nn.Linear(input_dimensions, hidden_dimensions)

        self.nonlinear = nn.ReLU()
    
        self.linear2 = nn.Linear(hidden_dimensions, output_dimensions)
    
    def forward(self, x):

        x = self.linear1(x)

        x = self.nonlinear(x)

        output = self.linear2(x)

        return output

In [99]:
# Define Fully Connected FF network for the Embedding model

class FFNetworkEmbedding(nn.Module):
    def __init__(self, input_dim, embedding_dim, output_dim):
        super(FFNetworkEmbedding, self).__init__()

        self.embed = nn.EmbeddingBag(input_dim, embedding_dim)

        self.linear1 = nn.Linear(embedding_dim, 64)
        self.linear2 = nn.Linear(64, 16)
        self.linear3 = nn.Linear(16, output_dim)

        self.relu = nn.ReLU()
        self.dropout = nn.Dropout(0.3)
        

    def forward(self, x, offsets):

        # apply an emedding bag layer to get average of all embeddings
        x = self.embed(x, offsets)

        # apply linear functions
        x = self.relu(self.linear1(x))
        x = self.relu(self.linear2(x))
        x = self.relu(self.linear3(x))

        # apply dropout to avoid overfitting
        x = self.dropout(x)

        return x
        

In [100]:
# define the dimensions of the basic model
input_dimensions = len(text_vocab) + len(titles_vocab) + 1
hidden_dimensions = 1000
output_dimensions = 1

# instantiate the class we are using for this model
model = FFNetwork(input_dimensions, hidden_dimensions, output_dimensions).to(device)

In [101]:
# define the dimensions of the basic model
input_dimensions_reg = 100
hidden_dimensions_reg = 1000
output_dimensions_reg = 1

# instantiate the class we are using for this model
model_reg = FFNetworkReg(input_dimensions_reg, hidden_dimensions_reg, output_dimensions_reg).to(device)

In [102]:
print(len(text_vocab), len(text_to_index))
print(len(titles_vocab), len(titles_to_index))
print(len(list(dict.fromkeys(text_vocab + titles_vocab))))

146851 146851
174165 174165
268481


In [103]:
# define dimensions of embedding model
input_dim_embed = len(text_vocab) + len(titles_vocab)
embedding_dim = 1024
output_dimensions_embed = 1

# instansiate the embedding model
model_embed = FFNetworkEmbedding(input_dim_embed, embedding_dim, output_dimensions_embed).to(device)

In [59]:
#it = iter(train_loader)
#print(model(torch.stack(next(it)["post"])))

In [104]:
# define loss functions class
# we choose to use BCEWithLogitsLoss as it provides the functionality of both a
# sigmoid layer and BCE loss in one. Is more efficient (look up details for diss)
loss_func = nn.BCEWithLogitsLoss()

In [105]:
# define optimizer class
learning_rate = 0.01
optimizer = torch.optim.SGD(model.parameters(), lr = learning_rate)

In [62]:

#for (batch_index, batch) in enumerate(train_loader):
#    if(batch_index > 0):
#        break
#    print(model(batch["post"]))

In [63]:
#for (batch_index, batch) in enumerate(train_loader):
#    if(batch_index > 0):
#        break
#    print(model_reg(batch["post"]))

In [106]:
# define function for calculating the accuracy of a model (current only used for BoW model)
def get_model_accuracy(model, loader):
    correct = 0
    total = 0

    for (batch_index, batch) in enumerate(loader):
        
        model.float()
        posts = batch["post"]
        scores = batch["score"]

        # get predirction probablities
        predictions_prob = model(posts)

        # get class predictions
        _, predictied = torch.max(predictions_prob.data, 1)

        # calculate tota samples predicted and correct
        total = total + scores.size(0)
        correct = correct + (predictied == scores).sum()

    accuracy = 100 * correct / total
    return accuracy,

In [107]:
# define function for training a model (also only usable for the BoW model)
def train_model(model, train_loader, test_loader, loss, optimizer):
    iteration = 0
    
    for epoch in range(num_epochs):
        print("Starting Epoch: " + str(epoch))
        for (batch_index, batch) in enumerate(train_loader):
            #print("Iteration " + str(iteration))
            model.float()
            posts = batch["post"]
            scores = batch["score"]

            # set grads to 0
            optimizer.zero_grad()

            predictions = model(posts)


            # calculate loss
            loss = loss_func(predictions, scores)

            # backwards pass to calculate gradients
            loss.backward()

            # update parameters
            optimizer.step()

            if iteration % 50 == 0:
                print("\n")
                accuracy = get_model_accuracy(model, test_loader)
                print("Iteration {}. Loss {}. Accuracy {}".format(iteration, loss.item(), accuracy))
                print("\n")

            iteration += 1

    return model

In [113]:
# define function for training a embedding model
def train_model_embed(model, train_loader, test_loader, loss, optimizer):
    iterations = 1
    accuracy_list = []
    loss_list = []

    # make sure model is being trained on gpu
    model.to(device)

    for epoch in range(num_epochs):
        print("Epoch {}.".format(epoch))
        running_loss = 0

        for index, batch in enumerate(train_loader):
            lables, texts, offsets = batch

            # set the model to track graidents for training
            model.train(True)

            # reset optimizer grads to zero
            optimizer.zero_grad()

            # forward pass of the model
            predictions = model(texts, offsets)

            # calculate loss
            loss = loss_func(predictions, lables.float())

            # perform backwards pass
            loss.backward()

            # tune weights with optimizer
            optimizer.step()

            # stop gradient tracking for writing current model metrics
            model.train(False)          

            # track the running loss
            running_loss += loss.item()

            if iterations % 100 == 0:

                print(" Iteration {}. Running Loss {}.".format( iterations, running_loss / 100))
    
                # reset running loss
                running_loss = 0

                """
                for test_index, test_batch in enumerate(test_loader):

                    test_lables, test_texts, test_offsets = test_batch

                    output_preds = model(test_texts, test_offsets)
                    output_preds = [1 if output > 0.0 else 0 for output in output_preds]

                    total = total + test_lables.size(0)

                    for i in range(len(test_lables)):
                        if output_preds[i] == test_lables[i]:
                            correct += 1
                

                accuracy = correct / total
                print("Iteration {}. Loss {}. Accuracy {}".format(iterations, loss.item(), accuracy))
                accuracy_list.append(accuracy)
                loss_list.append(loss.item())
                """
            iterations = iterations + 1
    return model, accuracy_list, loss_list

In [114]:
# train embedding model
model_embed_final, accs, losses = train_model_embed(model_embed, train_loader_embed, test_loader_embed, loss_func, optimizer)

Epoch 0.
 Iteration 100. Running Loss 0.6929555642604828.
 Iteration 200. Running Loss 0.6929392123222351.
 Iteration 300. Running Loss 0.6929160404205322.
 Iteration 400. Running Loss 0.6927888494729996.
 Iteration 500. Running Loss 0.6927948957681656.
 Iteration 600. Running Loss 0.6930310332775116.
 Iteration 700. Running Loss 0.6929505407810211.
 Iteration 800. Running Loss 0.6928647857904434.
 Iteration 900. Running Loss 0.6929511278867722.
 Iteration 1000. Running Loss 0.6929959571361541.
 Iteration 1100. Running Loss 0.6928664988279343.
 Iteration 1200. Running Loss 0.6929413878917694.
 Iteration 1300. Running Loss 0.6927529615163803.
 Iteration 1400. Running Loss 0.6930154514312744.
 Iteration 1500. Running Loss 0.6929141867160797.


KeyboardInterrupt: 

In [ ]:
# train BoW model
# currently this model takes way to long and takes up too much memory to work
model_final = train_model(model, train_loader, test_loader, loss_func, optimizer)